In [66]:
import geopandas as gpd
import numba
import numpy as np
import math

from feature.utils import timing
from parsers.utils import pcloud
from parsers.utils import raster

In [2]:
# class BufferableGeoDataFrame(gpd.GeoDataFrame):
#     def __init__(self, *args, **kwargs) -> None:
#         super().__init__()
# 
#     def buffer(self, *args, **kwargs) -> None:
#         ...

@timing
def __init__(filename: str) -> gpd.GeoDataFrame:
    return gpd.read_file(filename)


@timing
# TODO: Review the various buffer options.
# TODO: Rewrite this function as an appropriate class method.
def buffer(objs: gpd.GeoDataFrame, dist: float = 10) -> None:
    objs["geometry"] = objs["geometry"].buffer(dist)

## Step 1
Load the point cloud into memory.

In [3]:
pc = pcloud.PointCloud("../aula.LAZ")

func __init__ :-> 507 ms


## Step 2
Load the building footprints into memory.

In [4]:
fps = __init__("C:/Documents/RoofSense/data/temp/9-284-556.buildings.gpkg")

func __init__ :-> 574 ms


## Step 3
Buffer the footprints by 10 m.

NOTE: The buffer distance is selected such that most if not all the natural neighbors of 
      the points along the footprint edges are included in the subsequent steps.

In [5]:
buffer(fps)

func buffer :-> 88 ms


## Step 4
Intersect the point cloud with the buffers.

In [6]:
ids = pc.intersect(fps)

func intersect :-> 32879 ms


In [7]:
pc.las.points = pc.las.points[ids]

## Step 5
Compute the Delaunay triangulation of the remaining points.

In [8]:
pc.triangulate()

func triangulate :-> 8982 ms


## Step 6
 Estimate the slope field of the corresponding network.

TODO

In [9]:
# TOSELF: Promote this argument to an environment variable?
CELL_SIZE = 0.25

grid = raster.Raster(CELL_SIZE, pc.dt.get_bbox())

# FIXME: Integrate this block into the Raster initializer.
# Construct the grid.
# TODO: Add documentation.
rows, cols = np.mgrid[grid.height - 1:-1:-1, 0:grid.width]
# TODO: Add documentation.
xx = grid._bbox[0] + CELL_SIZE * (cols + 0.5)
yy = grid._bbox[1] + CELL_SIZE * (rows + 0.5)
# TODO: Add documentation.
cells = np.column_stack([xx.ravel(), yy.ravel()])

TODO

In [ ]:
# TODO: Speed up this block.
# TOSELF: Compute the slope for all faces to avoid additional calls to dt.locate?
valid_cells = []
valid_faces = []
for i, center in enumerate(cells):
    try:
        valid_faces.append(pc.dt.locate(*center))
    except Exception:
        continue
    valid_cells.append(i)

# TOSELF: Discard duplicate faces?
# valid_faces = np.unique(valid_faces, axis=0)

In [ ]:
# TODO: Add documentation.
dt_pts = pc.dt.points
valid_faces = np.array(valid_faces)
v1 = dt_pts[valid_faces[:, 0]]
v2 = dt_pts[valid_faces[:, 1]]
v3 = dt_pts[valid_faces[:, 2]]

u = v2 - v1
v = v3 - v1

n = np.cross(u, v)
n = n / np.linalg.norm(n, axis=1)[:, None]

z = np.array([0, 0, 1])
s = np.degrees(np.arccos(np.dot(n, z)))

In [ ]:
grid._data[np.divmod(valid_cells, grid.width)] = s
grid.save("../aula_slpe.tiff")

## Step 6
 Rasterize the slope and reflectance fields of the corresponding network.

In [ ]:
# Interpolate the field values at the cell centers.
vals = pc.dt.interpolate({"method": "Laplace"}, cells)

In [ ]:
# Populate the raster.
grid._data = vals.reshape((grid.height, grid.width))

# Save the raster.
grid.save("../aula_elev.tiff")

In [137]:
def laplace(
    dt: startinpy.DT, x: float, y: float, strict: bool = True
) -> tuple[list[int], list[float]]:
    num_pts = dt.number_of_vertices()
    if not num_pts:
        raise RuntimeError("The triangulation does not contain any vertices.")

    if strict:
        try:
            dt.locate(x, y)
        except Exception:
            raise ValueError(
                f"The interpolation point ({x, y}) is located outside the convex hull "
                f"of the triangulation."
            )

    pt_id = dt.insert_one_pt(x, y, 0)
    # The point was inserted at the same location as an existing vertex.
    if dt.number_of_vertices() == num_pts:
        return dt.points[pt_id, 2]

    # NOTE: This method does not walk the DT.
    if dt.is_vertex_convex_hull(pt_id):
        dt.remove(pt_id)
        raise ValueError(
            f"The interpolation point ({x, y}) is located on the boundary of the "
            f"convex hull of the triangulation."
        )

    pts = dt.points
    trs = dt.incident_triangles_to_vertex(pt_id)

    centers = []
    contrib = []
    for tr in trs:
        centers.append(circumcenter(pts[tr[0]], pts[tr[1]], pts[tr[2]]))
        contrib.append(tr[1])

    weights = []
    for i, cen in enumerate(centers):
        dx = centers[i - 1][0] - cen[0]
        dy = centers[i - 1][1] - cen[1]
        vor_edge = math.hypot(dx, dy)

        dx = pts[contrib[i]][0] - x
        dy = pts[contrib[i]][1] - y
        del_edge = math.hypot(dx, dy)

        weights.append(vor_edge / del_edge)

    attribs = [pts[con][2] for con in contrib]

    weights = np.array(weights)
    attribs = np.array(attribs)

    dt.remove(pt_id)
    return np.sum(attribs * weights) / np.sum(weights)


# NOTE: This function has been copied from `skspatial.objects.circle`.
def circumcenter(a, b, c):
    x_a, y_a, _ = a
    x_b, y_b, _ = b
    x_c, y_c, _ = c
    
    matrix = np.array(
        [
            [0, 0, 0, 1],
            [x_a**2 + y_a**2, x_a, y_a, 1],
            [x_b**2 + y_b**2, x_b, y_b, 1],
            [x_c**2 + y_c**2, x_c, y_c, 1],
        ],
    )

    M_00 = _minor(matrix, 0, 0)
    M_01 = _minor(matrix, 0, 1)
    M_02 = _minor(matrix, 0, 2)
    M_03 = _minor(matrix, 0, 3)

    x =  0.5 * M_01 / M_00
    y = -0.5 * M_02 / M_00
    return x, y


# NOTE: This function has been copied from `skspatial.objects.circle`.
def _minor(array, i: int, j: int):
    subarray = array[
        np.array(list(range(i)) + list(range(i + 1, array.shape[0])))[:, np.newaxis],
        np.array(list(range(j)) + list(range(j + 1, array.shape[1]))),
    ]
    return np.linalg.det(subarray)

In [140]:
temp=[]
for i, cell in enumerate(cells):
    print(f"{(i+1)}/{len(cells)}")
    try:
        # temp.append(laplace(pc.dt, *cell))
        temp.append(pc.dt.interpolate({"method": "Laplace"}, [cell]))
    except (RuntimeError, ValueError) as e:
        pass

grid._data = temp.reshape((grid.height, grid.width))
grid.save("../temp.tiff")

1/2391356
2/2391356
3/2391356
4/2391356
5/2391356
6/2391356
7/2391356
8/2391356
9/2391356
10/2391356
11/2391356
12/2391356
13/2391356
14/2391356
15/2391356
16/2391356
17/2391356
18/2391356
19/2391356
20/2391356
21/2391356
22/2391356
23/2391356
24/2391356
25/2391356
26/2391356
27/2391356
28/2391356
29/2391356
30/2391356
31/2391356
32/2391356
33/2391356
34/2391356
35/2391356
36/2391356
37/2391356
38/2391356
39/2391356
40/2391356
41/2391356
42/2391356
43/2391356
44/2391356
45/2391356
46/2391356
47/2391356
48/2391356
49/2391356
50/2391356
51/2391356
52/2391356
53/2391356
54/2391356
55/2391356
56/2391356
57/2391356
58/2391356
59/2391356
60/2391356
61/2391356
62/2391356
63/2391356
64/2391356
65/2391356
66/2391356
67/2391356
68/2391356
69/2391356
70/2391356
71/2391356
72/2391356
73/2391356
74/2391356
75/2391356
76/2391356
77/2391356
78/2391356
79/2391356
80/2391356
81/2391356
82/2391356
83/2391356
84/2391356
85/2391356
86/2391356
87/2391356
88/2391356
89/2391356
90/2391356
91/2391356
92/23913

KeyboardInterrupt: 